In [13]:
! git clone https://github.com/uf-hobi-informatics-lab/ClinicalTransformerNER.git

Cloning into 'ClinicalTransformerNER'...
remote: Enumerating objects: 143, done.
remote: Counting objects: 100% (143/143), done.
remote: Compressing objects: 100% (94/94), done.
remote: Total 143 (delta 76), reused 101 (delta 43), pack-reused 0
Receiving objects: 100% (143/143), 1019.89 KiB | 0 bytes/s, done.
Resolving deltas: 100% (76/76), done.


In [1]:
import sys
sys.path.append("./ClinicalTransformerNER/")
sys.path.append("./NLPpreprocessing-master/")

In [2]:
import os
from pathlib import Path
from collections import defaultdict, Counter
import numpy as np
from sklearn.model_selection import train_test_split
import shutil 

In [3]:
from annotation2BIO import generate_BIO, pre_processing, read_annotation_brat, BIOdata_to_file
MIMICIII_PATTERN = "\[\*\*|\*\*\]"

In [4]:
! ls

2018n2c2			       DR_ner.ipynb
all_annotated_notes_new		       DR_note_selection.ipynb
brat_eval.py			       log2.txt
ClinicalTransformerNER		       log.txt
ClinicalTransformerRelationExtraction  NLPpreprocessing-master


In [5]:
training_root = "./DR_notes/all_annotated_notes_new/"

In [6]:
i=0
file_ids=set()
for fn in Path(training_root).glob("*.ann"):
    file_ids.add(fn.stem)
    _, ens, _ = read_annotation_brat(fn)
    if len(ens)==0:
        print(fn)
#         fn_txt=str(fn).split('.')[0]+'.txt'
#         os.remove(fn)
#         os.remove(fn_txt)
#print(i)
    

DR_notes/all_annotated_notes_new/note_836.ann
DR_notes/all_annotated_notes_new/note_980.ann
DR_notes/all_annotated_notes_new/note_93.ann
DR_notes/all_annotated_notes_new/note_830.ann
DR_notes/all_annotated_notes_new/note_7753.ann
DR_notes/all_annotated_notes_new/note_658.ann
DR_notes/all_annotated_notes_new/note_933.ann
DR_notes/all_annotated_notes_new/note_737.ann


In [7]:
len(file_ids)


240

In [8]:
# Brief descriptive statistics
file_ids = set()
enss = []

for fn in Path(training_root).glob("*.ann"):
    file_ids.add(fn.stem)
    _, ens, _ = read_annotation_brat(fn)
    #print( _)
    enss.extend(ens)
print("training files: ", len(file_ids), list(file_ids)[:5])
print("total training eneitites: ", len(enss))
print("Entities distribution by types:\n", "\n".join([str(c) for c in Counter([each[1] for each in enss]).most_common()]))

training files:  240 ['1717357_note_4074', '2491473_note_7653', 'note_9335', '269536_note_700', '1952828_note_5361']
total training eneitites:  2472
Entities distribution by types:
 ('lesion', 1424)
('laterality', 696)
('severity', 311)
('eye_part', 41)


In [9]:
#split train and test annotation
file_ids = list(file_ids)
train_dev_ids, test_ids = train_test_split(file_ids, train_size=0.8, random_state=13, shuffle=True)
len(train_dev_ids), len(test_ids)
train_dev_root = Path('/home/zehao.yu/workspace/py3/dr_ann/DR_notes/used/train_set')
test_root = Path('/home/zehao.yu/workspace/py3/dr_ann/DR_notes/used/test_set')
#create notes file
Path(train_dev_root).mkdir(parents=True, exist_ok=True)
Path(test_root).mkdir(parents=True, exist_ok=True)
train_root=Path(training_root)
#copy file to train and test
for fid in train_dev_ids:
    txt_fn = train_root / (fid + ".txt")
    ann_fn = train_root / (fid + ".ann")
    txt_fn1 = train_dev_root / (fid + ".txt")
    ann_fn1 = train_dev_root / (fid + ".ann")
    shutil.copyfile(txt_fn, txt_fn1)
    shutil.copyfile(ann_fn, ann_fn1)
for fid in test_ids:
    txt_fn = train_root / (fid + ".txt")
    ann_fn = train_root / (fid + ".ann")
    txt_fn1 = test_root / (fid + ".txt")
    ann_fn1 = test_root / (fid + ".ann")
    shutil.copyfile(txt_fn, txt_fn1)
    shutil.copyfile(ann_fn, ann_fn1)

In [10]:
#test_root = Path('/home/zehao.yu/workspace/py3/dr_ann/diabetic_retinopathy/test_set')
file_ids = set()
enss = []

for fn in test_root.glob("*.ann"):
    file_ids.add(fn.stem)
    _, ens, _ = read_annotation_brat(fn)
    enss.extend(ens)
print("training files: ", len(file_ids), list(file_ids)[:5])
print("total training eneitites: ", len(enss))
print("Entities distribution by types:\n", "\n".join([str(c) for c in Counter([each[1] for each in enss]).most_common()]))

training files:  48 ['note_737', 'note_5937', 'note_5880', 'note_8392', 'note_6174']
total training eneitites:  486
Entities distribution by types:
 ('lesion', 280)
('laterality', 138)
('severity', 60)
('eye_part', 8)


In [11]:
# Brief descriptive statistics for train
file_ids = set()
enss = []

for fn in train_dev_root.glob("*.ann"):
    file_ids.add(fn.stem)
    _, ens, _ = read_annotation_brat(fn)
    enss.extend(ens)
print("training files: ", len(file_ids), list(file_ids)[:5])
print("total training eneitites: ", len(enss))
print("Entities distribution by types:\n", "\n".join([str(c) for c in Counter([each[1] for each in enss]).most_common()]))

training files:  192 ['1717357_note_4074', '2491473_note_7653', 'note_9335', '269536_note_700', '1952828_note_5361']
total training eneitites:  1986
Entities distribution by types:
 ('lesion', 1144)
('laterality', 558)
('severity', 251)
('eye_part', 33)


In [4]:
# generate BIO from brat annotation
train_root = train_dev_root
train_bio = "/home/zehao.yu/workspace/py3/dr_ann/DR_notes/bio/trains/"

output_root = Path(train_bio)
output_root.mkdir(parents=True, exist_ok=True)

for fid in file_ids:
    txt_fn = train_root / (fid + ".txt")
    ann_fn = train_root / (fid + ".ann")
    bio_fn = output_root / (fid + ".bio.txt")
    
    txt, sents = pre_processing(txt_fn, deid_pattern=MIMICIII_PATTERN)
    e2idx, entities, rels = read_annotation_brat(ann_fn)
    nsents, sent_bound = generate_BIO(sents, entities, file_id=fid, no_overlap=False)
    print(nsents)
    print(bio_fn)
    break
#     BIOdata_to_file(bio_fn, nsents)
#     print()
    #break

NameError: name 'train_dev_root' is not defined

In [13]:
# let us pick a file for check
! cat ./DR_notes/bio/trains/1737201_note_4194.bio.txt

OCT 0 3 0 3 O
, 3 4 4 5 O
Retina 5 11 6 12 O
- 12 13 13 14 O
OU 14 16 15 17 O
- 17 18 18 19 O
Both 19 23 20 24 B-laterality
Eyes 24 28 25 29 I-laterality
Without 33 40 30 37 O
IRF 41 44 38 41 B-lesion
/ 44 45 42 43 O
SRF 45 48 44 47 B-lesion
, 48 49 48 49 O
+ 50 51 50 51 O
RPED 51 55 52 56 O
OPH 60 63 57 60 O
- 64 65 61 62 O
OS 66 68 63 65 O
Intravitreal 69 81 66 78 O
Injection 82 91 79 88 O
, 91 92 89 90 O
Pharmacologic 93 106 91 104 O
Agent 107 112 105 110 O
Date 117 121 111 115 O
: 121 122 116 117 O
DATE 126 130 118 122 O
Patient 134 141 123 130 O
Name 142 146 131 135 O
: 146 147 136 137 O
NAME 151 155 138 142 O
Procedure 160 169 143 152 O
: 169 170 153 154 O
Intravitreal 171 183 155 167 O
Injection 184 193 168 177 O
, 193 194 178 179 O
OS 195 197 180 182 O
Intravitreal 199 211 183 195 O
Injection 212 221 196 205 O
Procedure 222 231 206 215 O
Note 232 236 216 220 O
Eye 238 241 221 224 O
: 241 242 225 226 O
OS 244 246 227 229 O
Pre 247 250 230 233 O
- 250 251 234 235 O
op 251 253 236

In [14]:
# now we have to split the train and dev sets
# for transformer NER, we need to name these two datasets as train.txt and dev.txt
file_ids = list(file_ids)
train_ids, dev_ids = train_test_split(file_ids, train_size=0.9, random_state=13, shuffle=True)
len(train_ids), len(dev_ids)

(172, 20)

In [15]:
# merge previous bio results into train.txt and dev.txt
import fileinput

# train
with open("./DR_notes/bio/train.txt", "w") as f:
    for fid in train_ids:
        f.writelines(fileinput.input(output_root / (fid + ".bio.txt")))
    fileinput.close()
        
# dev
with open("./DR_notes/bio/dev.txt", "w") as f:
    for fid in dev_ids:
        f.writelines(fileinput.input(output_root / (fid + ".bio.txt")))
    fileinput.close()
    
# now you can check your ./2018n2c2/bio, there should be two new files train.txt and dev.txt
! ls -l ./DR_notes/bio

total 2044
-rw-rw-r--. 1 zehao.yu zehao.yu  205471 Dec 21 03:21 dev.txt
drwxrwxr-x. 2 zehao.yu zehao.yu    8192 Dec 21 03:18 trains
-rw-rw-r--. 1 zehao.yu zehao.yu 1867980 Dec 21 03:21 train.txt


In [16]:
! cat ./DR_notes/bio/train.txt

Assessment 0 10 0 10 O
and 11 14 11 14 O
Plan 15 19 15 19 O
: 19 20 20 21 O
ICD 25 28 22 25 O
- 28 29 26 27 O
10 29 31 28 30 O
- 31 32 31 32 O
CM 32 34 33 35 O
ICD 35 38 36 39 O
- 38 39 40 41 O
9 39 40 42 43 O
- 40 41 44 45 O
CM 41 43 46 48 O
1 46 47 49 50 O
. 47 48 51 52 O

PDR 49 52 53 56 B-lesion
( 53 54 57 58 O
proliferative 54 67 59 72 B-lesion
diabetic 68 76 73 81 I-lesion
retinopathy 77 88 82 93 I-lesion
) 88 89 94 95 O
E11 90 93 96 99 O
. 93 94 100 101 O
3599 94 98 102 106 O
250.50 99 105 107 113 O
Fluorescein 106 117 114 125 O
Angiography 118 129 126 137 O
- 130 131 138 139 O
OU 132 134 140 142 B-laterality
- 135 136 143 144 O
Both 137 141 145 149 O
Eyes 142 146 150 154 O
362.02 150 156 155 161 O
OCT 157 160 162 165 O
, 160 161 166 167 O
Posterior 162 171 168 177 O
Segment 172 179 178 185 O
- 180 181 186 187 O
OU 182 184 188 190 O
- 185 186 191 192 O
Both 187 191 193 197 O
Eyes 192 196 198 202 O
2 198 199 203 204 O
. 199 200 205 206 O

TRD 201 204 207 210 O
( 205 206 211 212 O

The 2082 2085 2038 2041 O
patient 2086 2093 2042 2049 O
was 2094 2097 2050 2053 O
brought 2098 2105 2054 2061 O
to 2106 2108 2062 2064 O
the 2109 2112 2065 2068 O
examination 2113 2124 2069 2080 O
room 2125 2129 2081 2085 O
. 2129 2130 2086 2087 O

IC 2131 2133 2088 2090 O
was 2134 2137 2091 2094 O
confirmed 2138 2147 2095 2104 O
. 2147 2148 2105 2106 O

A 2149 2150 2107 2108 O
time 2151 2155 2109 2113 O
out 2156 2159 2114 2117 O
took 2160 2164 2118 2122 O
place 2165 2170 2123 2128 O
and 2171 2174 2129 2132 O
the 2175 2178 2133 2136 O
correct 2179 2186 2137 2144 O
eye 2187 2190 2145 2148 O
was 2191 2194 2149 2152 O
confirmed 2195 2204 2153 2162 O
with 2205 2209 2163 2167 O
patient 2210 2217 2168 2175 O
verbalization 2218 2231 2176 2189 O
. 2231 2232 2190 2191 O

A 2233 2234 2192 2193 O
drop 2235 2239 2194 2198 O
of 2240 2242 2199 2201 O
proparacaine 2243 2255 2202 2214 O
/ 2255 2256 2215 2216 O
tetracaine 2256 2266 2217 2227 O
and 2267 2270 2228 2231 O
then 2271 2275 2232 2236 O
a 2276

NAME 921 925 948 952 O
, 928 929 953 954 O
MD 930 932 955 957 O
participated 933 945 958 970 O
in 946 948 971 973 O
the 949 952 974 977 O
care 953 957 978 982 O
of 958 960 983 985 O
this 961 965 986 990 O
patient 966 973 991 998 O
. 973 974 999 1000 O

NAME 978 982 1001 1005 O
, 985 986 1006 1007 O
MD 987 989 1008 1010 O
Choroidal 991 1000 1011 1020 O
neuvs 1001 1006 1021 1026 O
OS 1007 1009 1027 1029 O
without 1010 1017 1030 1037 O
interval 1018 1026 1038 1046 O
changes 1027 1034 1047 1054 O
in 1035 1037 1055 1057 O
size 1038 1042 1058 1062 O
or 1043 1045 1063 1065 O
character 1046 1055 1066 1075 O
from 1056 1060 1076 1080 O
the 1061 1064 1081 1084 O
last 1065 1069 1085 1089 O
visit 1070 1075 1090 1095 O
. 1075 1076 1096 1097 O

Below 1078 1083 1098 1103 O
IRH 1084 1087 1104 1107 O
resolved 1088 1096 1108 1116 O
today 1097 1102 1117 1122 O
compared 1103 1111 1123 1131 O
to 1112 1114 1132 1134 O
last 1115 1119 1135 1139 O
visit 1120 1125 1140 1145 O
( 1126 1127 1146 1147 O
right 1127 1

. 3667 3668 3524 3525 O

Still 3669 3674 3526 3531 O
no 3675 3677 3532 3534 O
resolution 3678 3688 3535 3545 O
of 3689 3691 3546 3548 O
SRF 3692 3695 3549 3552 B-lesion
despite 3696 3703 3553 3560 O
d 3704 3705 3561 3562 O
/ 3705 3706 3563 3564 O
c 3706 3707 3565 3566 O
steroids 3708 3716 3567 3575 O
last 3717 3721 3576 3580 O
visit 3722 3727 3581 3586 O
. 3727 3728 3587 3588 O

IVFA 3729 3733 3589 3593 O
last 3734 3738 3594 3598 O
visit 3739 3744 3599 3604 O
showed 3745 3751 3605 3611 O
no 3752 3754 3612 3614 O
leakage 3755 3762 3615 3622 O
spot 3763 3767 3623 3627 O
indicative 3768 3778 3628 3638 O
of 3779 3781 3639 3641 O
another 3782 3789 3642 3649 O
process 3790 3797 3650 3657 O
. 3797 3798 3658 3659 O

Possible 3799 3807 3660 3668 O
very 3808 3812 3669 3673 O
viscous 3813 3820 3674 3681 O
long 3821 3825 3682 3686 O
standing 3826 3834 3687 3695 O
SRF 3835 3838 3696 3699 B-lesion
associated 3839 3849 3700 3710 O
with 3850 3854 3711 3715 O
superior 3855 3863 3716 3724 O
break 3864 3

significant 2696 2707 2636 2647 O
improvement 2708 2719 2648 2659 O
of 2720 2722 2660 2662 O
diabetic 2723 2731 2663 2671 O
macular 2732 2739 2672 2679 O
edema 2740 2745 2680 2685 O
. 2745 2746 2686 2687 O

Plan 2747 2751 2688 2692 O
for 2752 2755 2693 2696 O
IVA 2756 2759 2697 2700 O
# 2760 2761 2701 2702 O
4 2761 2762 2703 2704 O
OD 2763 2765 2705 2707 O
OS 2767 2769 2708 2710 O
- 2770 2771 2711 2712 O
s 2773 2774 2715 2716 O
/ 2774 2775 2717 2718 O
p 2775 2776 2719 2720 O
PPV 2777 2780 2721 2724 O
/ 2780 2781 2725 2726 O
retinectomy 2781 2792 2727 2738 O
and 2793 2796 2739 2742 O
PVR 2797 2800 2743 2746 O
removal 2801 2808 2747 2754 O
with 2809 2813 2755 2759 O
SO 2814 2816 2760 2762 O
. 2816 2817 2763 2764 O
Now 2818 2821 2766 2769 O
most 2822 2826 2770 2774 O
recently 2827 2835 2775 2783 O
s 2836 2837 2784 2785 O
/ 2837 2838 2786 2787 O
p 2838 2839 2788 2789 O
GDD 2840 2843 2790 2793 O
( 2844 2845 2794 2795 O
second 2845 2851 2796 2802 O
placement 2852 2861 2803 2812 O
) 2861 2862

and 680 683 679 682 O
then 684 688 683 687 O
a 689 690 688 689 O
drop 691 695 690 694 O
of 696 698 695 697 O
5 699 700 698 699 O
% 700 701 700 701 O
povidone 702 710 702 710 O
iodine 711 717 711 717 O
was 718 721 718 721 O
placed 722 728 722 728 O
in 729 731 729 731 O
the 732 735 732 735 O
treatment 736 745 736 745 O
eye 746 749 746 749 O
. 749 750 750 751 O

Lidocaine 751 760 752 761 O
gel 761 764 762 765 O
was 765 768 766 769 O
placed 769 775 770 776 O
in 776 778 777 779 O
the 779 782 780 783 O
inferior 783 791 784 792 O
fornix 792 798 793 799 O
. 798 799 800 801 O

A 800 801 802 803 O
bladed 802 808 804 810 O
eyelid 809 815 811 817 O
speculum 816 824 818 826 O
was 825 828 827 830 O
placed 829 835 831 837 O
in 836 838 838 840 O
the 839 842 841 844 O
eye 843 846 845 848 O
. 846 847 849 850 O

The 848 851 851 854 O
eye 852 855 855 858 O
was 856 859 859 862 O
marked 860 866 863 869 O
with 867 871 870 874 O
calipers 872 880 875 883 O
and 881 884 884 887 O
5 885 886 888 889 O
% 886 887 89

propranolol 4548 4559 4346 4357 O
( 4560 4561 4358 4359 O
INDERAL 4561 4568 4360 4367 O
) 4568 4569 4368 4369 O
20 4570 4572 4370 4372 O
MG 4573 4575 4373 4375 O
/ 4575 4576 4376 4377 O
5 4576 4577 4378 4379 O
ML 4577 4579 4380 4382 O
Solution 4580 4588 4383 4391 O
Take 4589 4593 4392 4396 O
7.5 4594 4597 4397 4400 O
mLs 4598 4601 4401 4404 O
by 4602 4604 4405 4407 O
mouth 4605 4610 4408 4413 O
3 4611 4612 4414 4415 O
times 4613 4618 4416 4421 O
daily 4619 4624 4422 4427 O
. 4624 4625 4428 4429 O

• 4629 4630 4430 4431 O
senna 4631 4636 4432 4437 O
( 4637 4638 4438 4439 O
SENOKOT 4638 4645 4440 4447 O
) 4645 4646 4448 4449 O
176 4647 4650 4450 4453 O
MG 4651 4653 4454 4456 O
/ 4653 4654 4457 4458 O
5 4654 4655 4459 4460 O
ML 4655 4657 4461 4463 O
Syrup 4658 4663 4464 4469 O
Take 4664 4668 4470 4474 O
350 4669 4672 4475 4478 O
mg 4673 4675 4479 4481 O
by 4676 4678 4482 4484 O
mouth 4679 4684 4485 4490 O
nightly 4685 4692 4491 4498 O
at 4693 4695 4499 4501 O
bedtime 4696 4703 4502 4509 O

In [25]:
os.environ['MKL_NUM_THREADS'] = '1'

In [20]:
"""
Next we will train the NER model
We will just use a BERT model pre-trained on general English corpora as an example

In general we need GPU to train the model, running with CPU the training will be extremely slow. 
We just give an demo here.  You can train you own model when you have GPU resources.

To use GPU, you just need to run 'export CUDA_VISIBLE_DEVICES=0' before run the training command
"""
#! MKL_THREADING_LAYER=GNU
! export CUDA_VISIBLE_DEVICES=-1  # indicate no GPU; if you have two GPUs then the IDs for them will be 0 and 1

! MKL_THREADING_LAYER=GNU python ./ClinicalTransformerNER/src/run_transformer_ner.py \
      --model_type bert \
      --pretrained_model bert-base-uncased \
      --data_dir ./DR_notes/bio \
      --new_model_dir ./saved_models/bert \
      --overwrite_model_dir \
      --max_seq_length 128 \
      --data_has_offset_information \
      --save_model_core \
      --do_train \
      --model_selection_scoring strict-f_score-1 \
      --do_lower_case \
      --train_batch_size 8 \
      --train_steps 1000 \
      --learning_rate 1e-5 \
      --num_train_epochs 20 \
      --gradient_accumulation_steps 1 \
      --do_warmup \
      --seed 13 \
      --warmup_ratio 0.1 \
      --max_num_checkpoints 3 \
      --log_file ./log2.txt \
      --progress_bar \
      --early_stop 3 

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertNerModel: ['cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertNerModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPretraining model).
- This IS NOT expected if you are initializing BertNerModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertNerModel were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.weight', 

In [21]:
! ls -l ./saved_models/bert

total 1711384
-rw-rw-r--. 1 zehao.yu zehao.yu        17 Dec 21 04:01 added_tokens.json
-rw-rw-r--. 1 zehao.yu zehao.yu       101 Dec 21 03:39 base_model_name.txt
-rw-rw-r--. 1 zehao.yu zehao.yu 438058313 Dec 21 03:52 checkpoint_1999.bin
-rw-rw-r--. 1 zehao.yu zehao.yu 438058313 Dec 21 03:42 checkpoint_418.bin
-rw-rw-r--. 1 zehao.yu zehao.yu 438058313 Dec 21 03:45 checkpoint_999.bin
-rw-rw-r--. 1 zehao.yu zehao.yu      1229 Dec 21 04:01 config.json
-rw-rw-r--. 1 zehao.yu zehao.yu       174 Dec 21 03:39 label2idx.json
-rw-rw-r--. 1 zehao.yu zehao.yu 438018551 Dec 21 03:52 pytorch_model.bin
-rw-rw-r--. 1 zehao.yu zehao.yu       112 Dec 21 04:01 special_tokens_map.json
-rw-rw-r--. 1 zehao.yu zehao.yu        48 Dec 21 04:01 tokenizer_config.json
-rw-rw-r--. 1 zehao.yu zehao.yu    231508 Dec 21 04:01 vocab.txt


In [39]:
cat ./log2.txt

2020-12-06 14:36:23 - Transformer_NER - INFO - Task will use cuda device: GPU_0.
2020-12-06 14:36:23 - Transformer_NER - WARNING - set tokenizer as bert-base-uncased
2020-12-06 14:36:23 - Transformer_NER - WARNING - set config as bert-base-uncased
2020-12-06 14:36:23 - Transformer_NER - INFO - Training/evaluation parameters: {'model_type': 'bert', 'pretrained_model': 'bert-base-uncased', 'config_name': 'bert-base-uncased', 'tokenizer_name': 'bert-base-uncased', 'data_dir': './diabetic_retinopathy/bio_les', 'data_has_offset_information': True, 'new_model_dir': './dr_bert_les', 'save_model_core': True, 'predict_output_file': None, 'overwrite_model_dir': True, 'seed': 13, 'max_seq_length': 128, 'do_train': True, 'model_selection_scoring': 'strict-f_score-1', 'do_predict': False, 'use_crf': False, 'do_lower_case': True, 'train_batch_size': 8, 'eval_batch_size': 8, 'train_steps': 1000, 'learning_rate': 1e-05, 'num_train_epochs': 20.0, 'gradient_accumulation_steps': 1, 'do_warmup': True, 'wa

In [22]:
"""
running prediction

In our transformer package, we have the format conversion between bio and brat; bioc implemented
"""

# generate bio
#test_root = Path('/home/zehao.yu/workspace/py3/dr_ann/diabetic_retinopathy/test_set_les')
test_bio = "/home/zehao.yu/workspace/py3/dr_ann/DR_notes/bio/test/"
output_root = Path(test_bio)
output_root.mkdir(parents=True, exist_ok=True)

for fn in test_root.glob("*.txt"):
    txt_fn = fn
    bio_fn = output_root / (fn.stem + ".bio.txt")
    
    txt, sents = pre_processing(txt_fn, deid_pattern=MIMICIII_PATTERN)
    nsents, sent_bound = generate_BIO(sents, [], file_id=fid, no_overlap=False)
    
    BIOdata_to_file(bio_fn, nsents)

2020-12-21 09:45:45,755 INFO sentence boundary detection class initiated.
2020-12-21 09:45:45,756 INFO word level tokenization with replace_number set to False
2020-12-21 09:45:45,757 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/DR_notes/used/test_set/2644164_note_8603.txt ...
2020-12-21 09:45:45,788 INFO process 2192394_note_6089 file
2020-12-21 09:45:45,835 INFO sentence boundary detection class initiated.
2020-12-21 09:45:45,836 INFO word level tokenization with replace_number set to False
2020-12-21 09:45:45,836 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/DR_notes/used/test_set/2183623_note_6078.txt ...
2020-12-21 09:45:45,857 INFO process 2192394_note_6089 file
2020-12-21 09:45:45,932 INFO sentence boundary detection class initiated.
2020-12-21 09:45:45,933 INFO word level tokenization with replace_number set to False
2020-12-21 09:45:45,933 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/DR_notes/used/test_set/note_2248.txt ...
2020-12-2

2020-12-21 09:45:47,349 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/DR_notes/used/test_set/2605770_note_8572.txt ...
2020-12-21 09:45:47,374 INFO process 2192394_note_6089 file
2020-12-21 09:45:47,422 INFO sentence boundary detection class initiated.
2020-12-21 09:45:47,423 INFO word level tokenization with replace_number set to False
2020-12-21 09:45:47,423 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/DR_notes/used/test_set/note_6094.txt ...
2020-12-21 09:45:47,431 INFO process 2192394_note_6089 file
2020-12-21 09:45:47,480 INFO sentence boundary detection class initiated.
2020-12-21 09:45:47,480 INFO word level tokenization with replace_number set to False
2020-12-21 09:45:47,482 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/DR_notes/used/test_set/844034_note_1211.txt ...
2020-12-21 09:45:47,497 INFO process 2192394_note_6089 file
2020-12-21 09:45:47,549 INFO sentence boundary detection class initiated.
2020-12-21 09:45:47,549 INFO word le

2020-12-21 09:45:48,973 INFO sentence boundary detection class initiated.
2020-12-21 09:45:48,975 INFO word level tokenization with replace_number set to False
2020-12-21 09:45:48,976 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/DR_notes/used/test_set/837304_note_1177.txt ...
2020-12-21 09:45:48,999 INFO process 2192394_note_6089 file


In [40]:

! export CUDA_VISIBLE_DEVICES=1

# use format 1 for BRAT, 2 for BioC, 0 as default for BIO
! MKL_THREADING_LAYER=GNU python ./ClinicalTransformerNER/src/run_transformer_batch_prediction.py \
      --model_type bert \
      --pretrained_model ./saved_models/bert \
      --raw_text_dir /home/zehao.yu/workspace/py3/dr_ann/DR_notes/used/test_set \
      --preprocessed_text_dir /home/zehao.yu/workspace/py3/dr_ann/DR_notes/bio/test/ \
      --output_dir ./dr_result_les \
      --max_seq_length 128 \
      --do_lower_case \
      --eval_batch_size 8 \
      --log_file ./log.txt\
      --do_format 1 \
      --do_copy \
      --data_has_offset_information

In [10]:
cat ./log.txt

2020-09-10 22:53:43 - Transformer_NER - INFO - Task will use cuda device: GPU_0.
2020-09-10 22:53:43 - Transformer_NER - WARNING - set tokenizer as bert-base-uncased
2020-09-10 22:53:43 - Transformer_NER - WARNING - set config as bert-base-uncased
2020-09-10 22:53:43 - Transformer_NER - INFO - Training/evaluation parameters: {'model_type': 'bert', 'pretrained_model': 'bert-base-uncased', 'config_name': 'bert-base-uncased', 'tokenizer_name': 'bert-base-uncased', 'data_dir': './diabetic_retinopathy/bio', 'data_has_offset_information': True, 'new_model_dir': './new_bert_ner_model', 'save_model_core': True, 'predict_output_file': None, 'overwrite_model_dir': True, 'seed': 13, 'max_seq_length': 128, 'do_train': True, 'model_selection_scoring': 'strict-f_score-1', 'do_predict': False, 'use_crf': False, 'do_lower_case': True, 'train_batch_size': 8, 'eval_batch_size': 8, 'train_steps': 1000, 'learning_rate': 1e-05, 'num_train_epochs': 20.0, 'gradient_accumulation_steps': 1, 'do_warmup': True, 

segment ids: [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
guards: [0, 1, 2, 2, 2, 3, 4, 5, 6, 7, 8, 9, 9, 10, 11, 12, 12, 12, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 22, 22, 22, 22, 23, 24, 25, 26, 27, 28, 29, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 39, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 55, 55, 56, 57, 58, 58, 59, 60, 61, 62, 63, 64, 65, 66, 66, 66, 67, 68, 69, 70, 70, 70, 71, 72, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
***********************************
            
2020-09-11 15:42:55 - Transformer_NER - INFO - 
************** Example *********

Subjective : History of Present Illness : NAME is a 25 y . o . male who is here today for f / u Cone dystrophy Review of Systems : Heart problems : no complaints Respiratory problems : sleep apnea General problems : no complaints ENT problems : hearing loss Gastrointestinal problems : no complaints Urinary problems : no complaints Skin problems : no complaints Musculoskeletal problems : no complaints Neurologic problems : developmental DELAY Psychiatric problems : no complaints Endocrine problems : hashimoto ' s Objective : Base Ophthalmology Exam Visual Acuity Right Left Dist cc 20 / 200 20 / 20 - Method : Snellen - Linear Correction : Glasses Tonometry Right Left Pressure 9 11 Method : Applanation Time : 9 : 34 AM Dilation Both eyes : 1.0 % Mydriacyl , 2.5 % Phenylephrine @ 9 : 39 AM Pupils Dark React APD Right 4 Minimal None Left 3 3 None Visual Fields Right Left Result Full Full Comments : Grossly Full OU difficult exam due to pt comprehension Extraocular Movement Right Left Result

input tokens: ['[CLS]', 'oh', '##t', '(', 'o', '##cular', 'hyper', '##tension', ')', ',', 'left', 'h', '##40', '.', '05', '##2', '365', '.', '04', 'humphrey', 'visual', 'field', '-', 'o', '##d', '-', 'right', 'eye', '(', '24', '-', '2', ')', 'oct', ',', 'optic', 'nerve', '-', 'ou', '-', 'both', 'eyes', '3', '.', '[SEP]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[

input tokens: ['[CLS]', 'cy', '##sto', '##id', 'mac', '##ular', 'ed', '##ema', ',', 'left', 'eye', 'h', '##35', '.', '352', '36', '##2', '.', '53', '2', '.', '[SEP]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD

input tokens: ['[CLS]', 'she', 'is', 'having', 'trouble', 'with', 'near', 'vision', 'and', 'would', 'like', 'a', 'change', 'in', 'her', 'reading', 'glasses', '.', '[SEP]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', '[PAD]', 

No Known Allergies Review of Systems : Heart problems : no complaints Respiratory problems : no complaints General problems : no complaints Objective : Patient Vitals for the past 8 hrs : BP Temp Temp src Pulse Resp SpO 2 Height Weight 01 / 30 / 17 1025 138 / 79 36.1 °C ( 97 °F ) Temporal 71 18 94 % 1.753 m ( 5 ' 9 " " ) 92.3 kg ( 203 lb 6.4 oz ) Pain Score Pain Scale ( UF ) - DVPRS : 0 Base Eye Exam Visual Acuity ( Snellen - Linear ) Right Left Dist sc 20 / 50 20 / 80 - 2 Tonometry ( iCare , 1 : 50 PM ) Right Left Pressure 9 10 Pupils Dark React APD Right 3 Brisk - - Left 3 Brisk - - Visual Fields Right Left Result Full Full Extraocular Movement Right Left Result Full , Ortho Full , Ortho Neuro / Psych Oriented x 3 : Yes Mood / Affect : Normal Dilation Slit Lamp and Fundus Exam Slit Lamp Exam Right Left Lids / Lashes Bleph Bleph Conjunctiva / Sclera Pinguecula Pinguecula Cornea pigmented guttata pigmented guttata Anterior Chamber Deep and quiet Deep and quiet Iris Round and reactive R

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [42]:

! python brat_eval.py --f1 ./DR_notes/used/test_set --f2 ./dr_result_formatted_output/

******************* Information Extraction Results *******************
                      ------- strict -------    ------ lenient -------
                      Prec.   Rec.    F(b=1)    Prec.   Rec.    F(b=1)
              Lesion  0.7300  0.8202  0.7725    0.7700  0.8652  0.8148
            Syndrome  0.0000  0.0000  0.0000    0.0000  0.0000  0.0000
            Eye_part  0.0000  0.0000  0.0000    0.0000  0.0000  0.0000
                      ------------------------------------------------
     Overall (micro)  0.7300  0.8066  0.7664    0.7700  0.8508  0.8084
     Overall (macro)  0.6994  0.7993  0.7251    0.7207  0.8225  0.7473

***************************** RELATIONS ******************************
             located  0.0000  0.0000  0.0000    0.0000  0.0000  0.0000
                      ------------------------------------------------
     Overall (micro)  0.0000  0.0000  0.0000    0.0000  0.0000  0.0000
     Overall (macro)  0.0000  0.0000  0.0000    0.0000  0.0000  0.0000

    

In [43]:
! python brat_eval.py --f1 ./diabetic_retinopathy/test_set_les/ --f2 ./dr_result_les_formatted_output/

******************* Information Extraction Results *******************
                      ------- strict -------    ------ lenient -------
                      Prec.   Rec.    F(b=1)    Prec.   Rec.    F(b=1)
              Lesion  0.7605  0.8453  0.8007    0.7961  0.8849  0.8382
            Eye_part  0.0000  0.0000  0.0000    0.0000  0.0000  0.0000
                      ------------------------------------------------
     Overall (micro)  0.7605  0.8393  0.7980    0.7961  0.8786  0.8353
     Overall (macro)  0.7643  0.8171  0.7775    0.7958  0.8563  0.8119

***************************** RELATIONS ******************************
             located  0.0000  0.0000  0.0000    0.0000  0.0000  0.0000
                      ------------------------------------------------
     Overall (micro)  0.0000  0.0000  0.0000    0.0000  0.0000  0.0000
     Overall (macro)  0.0000  0.0000  0.0000    0.0000  0.0000  0.0000

                                     35 files found                 


# new round

In [24]:
# generate bio
test_root = Path('/home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/')
test_bio = "./DR_notes/bio_new/"
output_root = Path(test_bio)
output_root.mkdir(parents=True, exist_ok=True)
file_ids = set()
# enss = []

# for fn in test_root.glob("*.ann"):
#     file_ids.add(fn.stem)
for fn in test_root.glob("*.txt"):
    txt_fn = fn
    bio_fn = output_root / (fn.stem + ".bio.txt")
    
    txt, sents = pre_processing(txt_fn, deid_pattern=MIMICIII_PATTERN)
    nsents, sent_bound = generate_BIO(sents, [], file_id=fn, no_overlap=False)
    
    BIOdata_to_file(bio_fn, nsents)

2021-01-01 19:08:29,657 INFO sentence boundary detection class initiated.
2021-01-01 19:08:29,658 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:29,659 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_1151.txt ...
2021-01-01 19:08:29,668 INFO process /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_1151.txt file
2021-01-01 19:08:29,714 INFO sentence boundary detection class initiated.
2021-01-01 19:08:29,715 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:29,715 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_1135.txt ...
2021-01-01 19:08:29,725 INFO process /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_1135.txt file
2021-01-01 19:08:29,773 INFO sentence boundary detection class initiated.
2021-01-01 19:08:29,773 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:29,774 INFO current processing /home/ze

2021-01-01 19:08:31,075 INFO sentence boundary detection class initiated.
2021-01-01 19:08:31,076 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:31,076 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_2502.txt ...
2021-01-01 19:08:31,084 INFO process /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_2502.txt file
2021-01-01 19:08:31,131 INFO sentence boundary detection class initiated.
2021-01-01 19:08:31,132 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:31,133 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_352.txt ...
2021-01-01 19:08:31,142 INFO process /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_352.txt file
2021-01-01 19:08:31,189 INFO sentence boundary detection class initiated.
2021-01-01 19:08:31,190 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:31,191 INFO current processing /home/zeha

2021-01-01 19:08:32,413 INFO sentence boundary detection class initiated.
2021-01-01 19:08:32,414 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:32,414 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_955.txt ...
2021-01-01 19:08:32,421 INFO process /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_955.txt file
2021-01-01 19:08:32,467 INFO sentence boundary detection class initiated.
2021-01-01 19:08:32,468 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:32,469 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_2760.txt ...
2021-01-01 19:08:32,477 INFO process /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_2760.txt file
2021-01-01 19:08:32,524 INFO sentence boundary detection class initiated.
2021-01-01 19:08:32,524 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:32,525 INFO current processing /home/zeha

2021-01-01 19:08:33,820 INFO sentence boundary detection class initiated.
2021-01-01 19:08:33,821 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:33,822 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_6901.txt ...
2021-01-01 19:08:33,839 INFO process /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_6901.txt file
2021-01-01 19:08:33,889 INFO sentence boundary detection class initiated.
2021-01-01 19:08:33,890 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:33,890 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_601.txt ...
2021-01-01 19:08:33,897 INFO process /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_601.txt file
2021-01-01 19:08:33,946 INFO sentence boundary detection class initiated.
2021-01-01 19:08:33,947 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:33,948 INFO current processing /home/zeha

2021-01-01 19:08:35,139 INFO sentence boundary detection class initiated.
2021-01-01 19:08:35,140 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:35,140 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_3595.txt ...
2021-01-01 19:08:35,148 INFO process /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_3595.txt file
2021-01-01 19:08:35,194 INFO sentence boundary detection class initiated.
2021-01-01 19:08:35,195 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:35,196 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_5227.txt ...
2021-01-01 19:08:35,204 INFO process /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_5227.txt file
2021-01-01 19:08:35,250 INFO sentence boundary detection class initiated.
2021-01-01 19:08:35,251 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:35,251 INFO current processing /home/ze

...

2021-01-01 19:08:44,301 INFO sentence boundary detection class initiated.
2021-01-01 19:08:44,302 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:44,302 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_7313.txt ...
2021-01-01 19:08:44,310 INFO process /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_7313.txt file
2021-01-01 19:08:44,359 INFO sentence boundary detection class initiated.
2021-01-01 19:08:44,360 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:44,360 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_5885.txt ...
2021-01-01 19:08:44,367 INFO process /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_5885.txt file
2021-01-01 19:08:44,413 INFO sentence boundary detection class initiated.
2021-01-01 19:08:44,414 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:44,415 INFO current processing /home/ze

2021-01-01 19:08:45,589 INFO sentence boundary detection class initiated.
2021-01-01 19:08:45,590 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:45,590 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_1574.txt ...
2021-01-01 19:08:45,599 INFO process /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_1574.txt file
2021-01-01 19:08:45,667 INFO sentence boundary detection class initiated.
2021-01-01 19:08:45,668 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:45,670 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_2603.txt ...
2021-01-01 19:08:45,683 INFO process /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_2603.txt file
2021-01-01 19:08:45,777 INFO sentence boundary detection class initiated.
2021-01-01 19:08:45,786 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:45,787 INFO current processing /home/ze

2021-01-01 19:08:46,921 INFO sentence boundary detection class initiated.
2021-01-01 19:08:46,922 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:46,922 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_6133.txt ...
2021-01-01 19:08:46,930 INFO process /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_6133.txt file
2021-01-01 19:08:46,977 INFO sentence boundary detection class initiated.
2021-01-01 19:08:46,978 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:46,979 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_370.txt ...
2021-01-01 19:08:46,989 INFO process /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_370.txt file
2021-01-01 19:08:47,037 INFO sentence boundary detection class initiated.
2021-01-01 19:08:47,038 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:47,039 INFO current processing /home/zeha

2021-01-01 19:08:48,166 INFO sentence boundary detection class initiated.
2021-01-01 19:08:48,167 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:48,167 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_8404.txt ...
2021-01-01 19:08:48,176 INFO process /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_8404.txt file
2021-01-01 19:08:48,224 INFO sentence boundary detection class initiated.
2021-01-01 19:08:48,225 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:48,225 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_1753.txt ...
2021-01-01 19:08:48,233 INFO process /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_1753.txt file
2021-01-01 19:08:48,281 INFO sentence boundary detection class initiated.
2021-01-01 19:08:48,282 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:48,282 INFO current processing /home/ze

2021-01-01 19:08:49,395 INFO sentence boundary detection class initiated.
2021-01-01 19:08:49,395 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:49,396 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_7783.txt ...
2021-01-01 19:08:49,404 INFO process /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_7783.txt file
2021-01-01 19:08:49,451 INFO sentence boundary detection class initiated.
2021-01-01 19:08:49,452 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:49,452 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_8649.txt ...
2021-01-01 19:08:49,460 INFO process /home/zehao.yu/workspace/py3/dr_ann/DR_notes/new_round/note_8649.txt file
2021-01-01 19:08:49,508 INFO sentence boundary detection class initiated.
2021-01-01 19:08:49,508 INFO word level tokenization with replace_number set to False
2021-01-01 19:08:49,509 INFO current processing /home/ze

In [25]:

#round2
! export CUDA_VISIBLE_DEVICES=1

# use format 1 for BRAT, 2 for BioC, 0 as default for BIO
! MKL_THREADING_LAYER=GNU python ./ClinicalTransformerNER/src/run_transformer_batch_prediction.py \
      --model_type bert \
      --pretrained_model ./saved_models/bert \
      --raw_text_dir ./DR_notes/new_round/ \
      --preprocessed_text_dir ./DR_notes/bio_new \
      --output_dir ./DR_result/new_round_result \
      --max_seq_length 128 \
      --do_lower_case \
      --eval_batch_size 8 \
      --log_file ./log3.txt\
      --do_format 1 \
      --do_copy \
      --data_has_offset_information

In [10]:
cat ./log3.txt

2021-05-18 15:49:03 - Transformer_NER - INFO - Task will use cuda device: GPU_0.
2021-05-18 15:49:03 - Transformer_NER - INFO - load checkpoint from saved_models/bert/checkpoint_1999.bin


# relation

In [6]:
! git clone https://github.com/uf-hobi-informatics-lab/ClinicalTransformerRelationExtraction.git

Cloning into 'ClinicalTransformerRelationExtraction'...
remote: Enumerating objects: 108, done.
remote: Counting objects: 100% (108/108), done.
remote: Compressing objects: 100% (61/61), done.
remote: Total 108 (delta 58), reused 96 (delta 46), pack-reused 0
Receiving objects: 100% (108/108), 41.57 KiB | 0 bytes/s, done.
Resolving deltas: 100% (58/58), done.


In [5]:
! export CUDA_VISIBLE_DEVICES=0  # indicate no GPU; if you have two GPUs then the IDs for them will be 0 and 1
#MKL_THREADING_LAYER=GNU
! MKL_THREADING_LAYER=GNU python ./ClinicalTransformerNER/src/run_transformer_ner.py \
      --model_type bert \
      --pretrained_model bert-base-uncased \
      --data_dir ./diabetic_retinopathy/bio_les \
      --new_model_dir ./dr_bert_les \
      --overwrite_model_dir \
      --max_seq_length 128 \
      --data_has_offset_information \
      --save_model_core \
      --do_train \

export CUDA_VISIBLE_DEVICES=1
data_dir=./sample_data
nmd=./new_model
pof=./predictions.txt
log=./log.txt

python ./ClinicalTransformerRelationExtraction/src/relation_extraction.py \
		--model_type bert \
		--data_format_mode 0 \
		--classification_scheme 2 \
		--pretrained_model bert-base-uncased \
		--data_dir $data_dir \
		--new_model_dir $nmd \
		--predict_output_file $pof \
		--overwrite_model_dir \
		--seed 13 \
		--max_seq_length 256 \
		--cache_data \
		--do_train \
		--do_predict \
		--do_lower_case \
		--train_batch_size 4 \
		--eval_batch_size 4 \
		--learning_rate 1e-5 \
		--num_train_epochs 3 \
		--gradient_accumulation_steps 1 \
		--do_warmup \
		--warmup_ratio 0.1 \
		--weight_decay 0 \
		--max_num_checkpoints 1 \
		--log_file $log \

str